In [1]:
!pip install transformers diffusers accelerate ipywidgets

     ━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━ 44.4/44.4 kB 1.3 MB/s eta 0:00:00
     ━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━ 40.5/40.5 kB 3.2 MB/s eta 0:00:00
   ━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━ 9.9/9.9 MB 45.4 MB/s eta 0:00:0000:0100:01
   ━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━ 2.7/2.7 MB 44.9 MB/s eta 0:00:00a 0:00:01
   ━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━ 324.4/324.4 kB 31.0 MB/s eta 0:00:00
   ━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━ 436.4/436.4 kB 37.6 MB/s eta 0:00:00
   ━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━ 792.8/792.8 kB 41.9 MB/s eta 0:00:00
   ━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━ 435.0/435.0 kB 31.3 MB/s eta 0:00:00
   ━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━ 2.9/2.9 MB 52.9 MB/s eta 0:00:00:00:01


In [2]:
import torch
from diffusers import StableDiffusionPipeline
from matplotlib import pyplot as plt
import datetime

In [3]:
# diffusers docs: https://huggingface.co/docs/diffusers/api/pipelines/stable_diffusion/text2img#texttoimage-generation
# model_id = "dreamlike-art/dreamlike-diffusion-1.0"
# model_id = "prompthero/openjourney"
# model_id = "XpucT/Deliberate"
model_id = "dreamlike-art/dreamlike-photoreal-2.0"

In [4]:
pipe = StableDiffusionPipeline.from_pretrained(model_id, torch_dtype=torch.float16, safety_checker=None)
device = "cuda" if torch.cuda.is_available() else "mps" if torch.backends.mps.is_available() else "cpu"
pipe = pipe.to(device)

Loading pipeline components...:   0%|          | 0/5 [00:00<?, ?it/s]

/opt/conda/lib/python3.11/site-packages/transformers/tokenization_utils_base.py:1617: FutureWarning: `clean_up_tokenization_spaces` was not set. It will be set to `True` by default. This behavior will be deprecated in transformers v4.45, and will be then set to `False` by default. For more details check this issue: https://github.com/huggingface/transformers/issues/31884
  warnings.warn(


In [5]:
import numpy as np
import ipywidgets as widgets
from IPython.display import clear_output, display

import matplotlib.pyplot as plt
from IPython.display import set_matplotlib_formats
%matplotlib inline
#set_matplotlib_formats('svg')

np.random.seed(42)

#prompt = "Renaissance-style portrait of an astronaut in space, detailed starry background, reflective helmet, matte painting, hyperdetailed, CGSociety"
#negative_prompt = "gold"
#textarea
std_layout = widgets.Layout(width="auto")

prompt_box = widgets.Textarea(value='', placeholder='cats, sharks, ships, underwater, cinematic composition', description='', layout=widgets.Layout(height="50px", width="auto"))
neg_prompt_box = widgets.Textarea(value='', placeholder='negative prompt', description='', layout=widgets.Layout(height="30px", width="auto"))
#slider 
img2gen_lab = widgets.Label(value="Images to Generate:", layout=std_layout)
img2gen_var = widgets.IntSlider(value=1, min=1, max=10, layout=std_layout)
#input
size_x_lab = widgets.Label(value="Image Width:", layout=std_layout)
size_x_var = widgets.BoundedIntText(value=32, min=32, max=512, step=8, layout=std_layout)
size_y_lab = widgets.Label(value="Image heigth:", layout=std_layout)
size_y_var = widgets.BoundedIntText(value=32, min=32, max=512, step=8, layout=std_layout)
steps_lab = widgets.Label(value="Steps:", layout=std_layout)
steps_var = widgets.BoundedIntText(value=50, min=11, max=100, step=1, layout=std_layout)
#Button
btn = widgets.Button(description="Generate", tooltip="Click me",
    layout=widgets.Layout(width="auto", height="30px", margin="30px"))
#Canvas
fig = plt.figure(figsize=(128/80, 128/80))
box = widgets.VBox([prompt_box, neg_prompt_box, img2gen_lab, img2gen_var, steps_lab, steps_var, size_x_lab, size_x_var,size_y_lab, size_y_var, btn])
box2 = widgets.VBox([prompt_box, neg_prompt_box, img2gen_lab, img2gen_var, steps_lab, steps_var, size_x_lab, size_x_var,size_y_lab, size_y_var, btn])

box2

<Figure size 160x160 with 0 Axes>

In [6]:
out = widgets.Output()
out

Output()

In [7]:
def on_value_change(change):
    prompt = prompt_box.value
    negative_prompt = neg_prompt_box.value
    images_to_generate = int(img2gen_var.value)
    steps = steps_var.value
    width = size_x_var.value
    height = size_y_var.value
    seed = None
    guidance = 7.5 # Higher guidance scale encourages to generate images that are closely linked to the text prompt, usually at the expense of lower image quality.
    with out:
        clear_output(wait=True)
        for _ in range(images_to_generate):
            steps = int(steps)
            width = int(width)
            height = int(height)
            current_seed = seed or torch.randint(0, int(1e5), size=(1, 1))[0].item()
            generator = torch.Generator().manual_seed(int(current_seed))
            img = pipe(prompt=prompt, negative_prompt=negative_prompt, width=width, height=height, num_inference_steps=steps, guidance_scale=guidance, generator=generator).images[0]
            time_now = datetime.datetime.now().strftime("%y.%m.%d_%H:%M:%S")
            plt.imshow(img)
            plt.axis("off")
            print("Current Seed:", current_seed)
            plt.title("")
            plt.show()
         #  img.save(f"./{time_now}_{current_seed}.jpg")

btn.on_click(on_value_change)

